# TP 8 : Diagnostic de la régression : analyse des observations
Le but du TP est de réaliser un diagnostic d'un modèle de régression d'un point de vue général, ainsi que via l'observation des variables. Ce TP vous permettra d'implémenter le calcul du $R^2$, ainsi que des coefficients de levier et de contribution.

| Numéro        | Compétence           | 
|:------------- |:--------------------:|
|PY502|	Afficher un résumé du diagnostic de la régression et savoir l’analyser|
|RL203|	Savoir analyser les résidus de régression|
|RL204|	Comprendre la définition de l’effet levier d’une observation|
|RL205|	Comprendre la définition de la contribution d’un couple|


In [ ]:
import numpy as np
import matplotlib.pyplot as plt

## Ex. 1 — Détection de points aberrants dans la régression
On considère les n = 11 observations suivantes :

i| 1| 2 |3| 4| 5| 6| 7| 8| 9 |10| 11
---|---|---|---|---|---|---|---|---|---|---|---
x | -1.0782 |0.0838| 0.1524 |0.2290| 0.4427| 0.4505| 0.5383| 0.8258| 0.9133| 0.9961| 3.0597
y| -0.8307| 0.1538 |0.0926| 0.2336| 0.3903| 0.1005| 0.4812 |0.6595| 0.7175| 0.7648 |0.3519

Les observations $y$ sont liées aux $x$ à travers le modèle linéaire :
$y_i = ax_i + b + \epsilon_i \text{, avec    } i = 1, n$
où les $\epsilon_i$ sont des variables aléatoires i.i.d. distribuées selon une loi normale centrée de variance
$\sigma^2$ inconnue et $(a, b)$ sont deux paramètres inconnus.

1. Effectuons les calculs liés au modèle de régression et à son diagnostic.

    a) construire une matrice $X$ et un vecteur $y$ contenant les données de la régression que l’on souhaite effectuer.

In [ ]:
data = np.array([
    [1, -1.0782, -.8307],
    [2, 0.0838, 0.1538],
    [3, 0.1524, 0.0926],
    [4, 0.2290, 0.2336],
    [5, 0.4427, 0.3903],
    [6, 0.4505, 0.1005],
    [7, 0.5383, 0.4812],
    [8, 0.8258, 0.6595],
    [9, 0.9133, 0.7175],
    [10, 0.9961, 0.7648],
    [11, 3.0597, 0.3519]
])
X = ...
y = ...


In [ ]:
n, _ = data.shape
p = 1
X=np.stack([np.ones((n,)), data[:,1]], axis=-1)
y = data[:,2]


a) Calculer l’estimation de $a$ et $b$ sens des moindres carrés

In [ ]:
...
a = ...
b = ...

In [ ]:
alpha = np.linalg.solve(X.T@X,X.T@y)
a = alpha[1]
b = alpha[0]
a, b

b) Plotter $x$ et $y$, ainsi que votre droite de régression.

In [ ]:
plt.plot(X[:,1],y,'o')
z = X@alpha
plt.plot(x,z,'x-')
plt.show()

c) Calculer des résidus et une estimation non biaisée de la variance des erreurs $\sigma^2$.
> **Aide** Combien de degré de libertés pour les résidus ?

In [ ]:
e = y - z
s2 = np.sum(e**2)/(n-2) #Moyenne des residus à 0; n -p-1 ddl, ici p=1
print(s2)
print(np.mean(e))

d) Évaluer la qualité globale de la régression

In [ ]:
SCT = np.sum((y-np.mean(y))**2)
SCE = np.sum(e**2)
R2 = 1 - SCE/SCT #plein de manieres de calculer
R2

e) Calculer le levier de chaque observation. Affichez les valeurs sous forme d'un graphique en barres.

D'après le cours : 
$$
H = X (X^\top X)^{-1}X^\top
$$
les leviers de chaque point sont les $H_{ii}$
 on peut aussi écrire : 
 $$
 H = X G
 $$
 avec 
 $$
 G = (X^\top X)^{-1}X^\top
 $$
 La matrice $G$ est donc aussi solution des $n$ systèmes linéaires : 
 $$
 (X^\top X) \; G = X^\top
 $$

In [ ]:
h = ...

In [ ]:
H = X@np.linalg.inv(X.T@X)@X.T
H = X@np.linalg.solve(X.T@X,X.T)  # plus stable et plus rapide
h = np.diag(H)
print(h)
plt.bar(range(n),h)

g) Calculer la contribution de chaque observation. Idem, affichez les valeur sous forme de graphiques en barres.

In [ ]:
c = ...

d'après le cours 
$$
    c_i = \frac{H_{ii}}{(1 - H_{ii})^2}\frac{\hat \varepsilon_i^2}{p s^2}
$$

In [ ]:
c = h/((1-h)**2)*(e**2)/(p*s2)
plt.bar(np.arange(n),c)
print(c)

h) Visualisez tous ces résultats dans un tableau contenant le vecteur des observations
$x$, le vecteur des réponses $y$, les prédiction du modèle, les résidus, les leviers, les
contributions et une variable binaire repérant les points dont la contribution dépasse
$4/n$. Ces résultats vous paraissent ils cohérents ?

In [ ]:
res = np.array([x, y, z, e, h, c , c>(4/n)])
print('-------------------------------------------------------')
print('      x      y      z     e      h      c   Aberrant ?')
print('-------------------------------------------------------')
with np.printoptions(precision=3, suppress=True):
    print(res.T)

2. Nous allons maintenant « consolider » ces résultats en écrivant une fonction réutilisable (et par la même nous abstraire du copier/coller et de ces effets néfastes).
    
a) Écrire une fonction Python ma_reg permettant d’intégrer les calculs fait précédemment. Votre fonction prendra la matrice $X$ et le vecteur $y$ comme paramètres d’entrée et retournera :
   
- l’estimation des paramètres de la régression sens des moindres carrés,
- une estimation de la variance des erreurs $\sigma^2$,
- le coefficient de détermination $R^2$
- une matrice n × 3 contenants des éléments permettant de réaliser le diagnostic de la régression à savoir :
    - les résidus,
    - le levier de chaque observation,
    - la contribution de chaque observation.

In [ ]:
def ma_reg(X,y):
    pass

In [ ]:
def ma_reg(X,y): #a voir avec les eleves si ils veulent avoir X avec la colonne de 1 intégré ou pas
    '''
    X : matrice de taille n par p+1, avec derniere colonne de 1
    '''
    n,p = X.shape
    a = np.linalg.solve(X.T@X,X.T@y)
    z = X@a
    e = y - z 
    s2 = np.sum(e**2)/(n-p) # ici le nb de col de X est p+1
    SCT = np.sum((y-np.mean(y))**2)
    SCE = np.sum(e**2)
    R2 = 1 - SCE/SCT
    H = X@np.linalg.solve(X.T@X,X.T)  # plus stable et plus rapide
    h = np.diag(H)
    c = h/((1-h)**2)*(e**2)/(p*s2)
    
    dv = np.stack([e, h, c], axis=-1)
    
    return a, s2, R2, dv

c) Écrire un script Python permettant de tester cette fonction. Que constatez vous ?

In [ ]:
a, s2, R2, diagd = ma_reg(X,y)
a,s2,R2, diagd
# le dernier point est suspect !

Sans le dernier point, la regression est bien meilleure

d) Que se passe t’il si l’on exécute les instruction suivantes ?

In [ ]:
yp = X
a, s2, R2, diagd = ma_reg(X,yp)

la fonction ma_reg attend une matrice X de taille $n \times p$ ce qui est bon, et un vecteur de taille $n$. Ici, à la place de ce vecteur, on passe en paramètre une matrice yp de taille $n \times p$ puisqu'il s'agit de $X$ !

e) Ajouter au début de la fonction ma_reg un test permettant de vérifier que les dimensions de la matrice $X$ et du vecteur $y$ sont bien conformes

In [ ]:
def ma_reg(X,y):
    pass

In [ ]:
def ma_reg(X,y):
    '''
    X : numpy array de dimention n x p
    y : numpy array de dimention n
    '''
    n,p = X.shape
    m = np.prod(y.shape)
    if n != m:
        raise Exception('X doit etre une matrice de n lignes et p colonnes et y un vecteur de n lignes')
        
    a = np.linalg.solve(X.T@X,X.T@y)
    z = X@a
    e = y - z # z - y
    s2 = np.sum(e**2)/(n-2)
    SCT = np.sum((y-np.mean(y))**2)
    SCE = np.sum(e**2)
    R2 = 1 - SCE/SCT
    H = X@np.linalg.solve(X.T@X,X.T)  # plus stable et plus rapide
    h = np.diag(H)
    c = h/((1-h)**2)*(e**2)/(p*s2)
    
    dv = np.stack([e, h, c])
    
    return a, s2, R2, dv

a, s2, R2, diagd = ma_reg(X,y)
#yp = X
#a, s2, R2, diagd = ma_reg(X,yp)
print(diagd.T)

3\. Effectuer le diagnostic de la régression
    
a) trouver une observation avec un résidu important et un faible levier

C'est le cas de l'avant dernier point. 

b) trouver une observation avec un faible résidu et un fort levier
    
   

 point 1 
 

c) trouver une observation avec un fort résidu et un levier important. Vérifier que vous avez bien détecté qu’il s’agit d’un point aberrant.
    
 

   dernier point

  
d) Après avoir éliminé le point aberrant, refaire toutes les étapes de la régression

In [ ]:
Xn = np.delete(X, -1, 0)
yn = np.delete(y, -1 ,0)
a2, s22, R22, D2 = ma_reg(Xn,yn)

plt.subplot(2,1,1)
plt.plot(Xn[:,1],yn,'o')
plt.plot(Xn[:,1],Xn@a,'r--')
plt.plot(Xn[:,1],Xn@a2,'g-')

plt.subplot(2,1,2)
plt.plot(Xn[:,1], D2[0,:],'*m')
plt.grid()
plt.show()

xa = Xn@a2
print('-------------------------------------------- ')
print('     x     y      z      e      h      c    ')
print('-------------------------------------------- ')
R = np.stack([Xn[:,1], yn[:], xa[:], D2[0,:], D2[1,:], D2[2,:]],axis=-1)
with np.printoptions(precision=3, suppress=True):
    print(R)
    
plt.plot(x,y,'o')
z = X@a
plt.plot(x,z,'x-')
zn = X@an
plt.plot(x,zn,'x-')
plt.legend(['les observations','la régression acvec tous ','la régression sans le dernier point'])
plt.show()

a) trouver une observation avec un résidu important et un faible levier
    
C'est le cas du 6ème point dans la régression 
    
b) trouver une observation avec un faible résidu et un fort levier
    
C'est le cas du premier point ($H_{11} = 0.75$)

## Ex. 2 — Modèle mal spécifié
On considère les n = 11 observations suivantes :

x| 1.00 |1.50| 2.00| 2.50| 3.00| 3.50| 4.00| 4.50| 5.00| 5.50| 6.0000
---|---|---|---|---|---|---|---|---|---|---|---|
y| 5.10| 4.56| 4.85| 7.48| 9.10| 11.65| 14.87| 19.20| 24.23| 32.10| 39.80

1. Effectuer le régression linéaire entre x et y et déterminer le coefficient de corrélation et visualiser les résidus. Ces résidus sont-ils conformes aux hypothèses de la régression ?

In [ ]:
data = np.array([[1, 5.1],
                [1.5, 4.56],
                [2, 4.85],
                [2.5, 7.48],
                [3, 9.1],
                [3.5, 11.65],
                [4, 14.87],
                [4.5, 19.2],
                [5, 24.23],
                [5.5, 32.1],
                [6, 39.8]])


In [ ]:

x = data[:,0]
y = data[:,1]
n = len(x)
X = np.stack([np.ones((n,)), x], axis=-1)

(a, s2, R2i, diagd) = ma_reg(X,y)
z = X@a
e = diagd[0,:]

plt.subplot(3,1,1)
plt.plot(x,y,'o')
plt.plot(x,z,'r-')
plt.subplot(3,1,2)
plt.plot(x,e,'o')
plt.show() # non, ils ne suivent pas  une loi normale mais on une structure

2\. Effectuer la régression polynomiale (degré 2) entre x et y et déterminer le coefficient de détermination. La régression polynomiale consiste à faire l’hypothèse que les observations $y$ sont liées aux $x$ à travers le modèle quadratique :

$y_i = a_0 + a_1x_i + a_2x^2_i + \epsilon_i\text{, avec } i = 1, n$

où les $\epsilon_i$ sont des variables aléatoires i.i.d. distribuées selon une loi normale centrée de
variance $\sigma^2$ inconnue et $(a_0, a_1, a_2)$ sont trois paramètres inconnus.

In [ ]:
X = np.stack([np.ones((n,)), x, x**2], axis=-1)
a, s2, R2f, diagd = ma_reg(X,y)
print(R2f)

3\. Visualiser les résidus de la régression et vérifier qu’ils vérifient bien les hypothèses de la régression.

In [ ]:
plt.subplot(3,1,1)
plt.plot(x,y,'o')
z = X@a
plt.plot(x,z,'r-')
plt.subplot(3,1,2)
e = diagd[0,:]
plt.plot(x,e,'o')
plt.show()

4\. Comparez les coefficients de détermination des deux régressions.

In [ ]:
print(R2i)
print(R2f)